In [422]:
import requests
from bs4 import BeautifulSoup
import re
import pandas as pd
import numpy as np
import json
from datetime import datetime, timedelta

## NFL

In [427]:
# Web scrape Draft Kings NFL page forthe games available
url = "https://sportsbook.draftkings.com/leagues/football/88670561"
response = requests.get(url)
soup = BeautifulSoup(response.text, "html.parser")

In [428]:
# Narrow the Beautiful Soup extract to just the field of interest "window.__INITIAL_STATE__"

# Filter out opening and closing <script> tags
nfl_scrape = str(list(list(list(soup.children)[2])[3])[11]).replace("<script>","").replace("</script>", "")
# Remove leading and trailing whitespace
nfl_scrape = nfl_scrape.strip()
# Split sections
nfl_scrape = nfl_scrape.split(";\n")
# Isolate to json of interest
nfl_scrape = nfl_scrape[6].strip()
# Format as json dictionary
nfl_scrape = nfl_scrape.replace("window.__INITIAL_STATE__ = ","")
nfl_scrape = json.loads(nfl_scrape)
nfl_scrape

{'eventGroups': {'88670561': {'eventGroupId': 88670561,
   'providerEventGroupId': '88808',
   'providerId': 2,
   'displayGroupId': 5313,
   'name': 'NFL',
   'offerCategories': [{'name': 'Game Lines',
     'offerSubcategoryDescriptors': [{'name': 'Game',
       'offerSubcategory': {'name': 'Game',
        'subcategoryId': 4518,
        'componentId': 210,
        'betTypeIds': [1, 6, 2],
        'offerSortOrder': ['2_56068722',
         '3_56068722',
         '1_56068722',
         '2_56068661',
         '3_56068661',
         '1_56068661',
         '2_56068667',
         '3_56068667',
         '1_56068667',
         '2_56068711',
         '3_56068711',
         '1_56068711',
         '2_56068693',
         '3_56068693',
         '1_56068693',
         '2_56068700',
         '3_56068700',
         '1_56068700',
         '2_56068676',
         '3_56068676',
         '1_56068676',
         '2_56068679',
         '3_56068679',
         '1_56068679',
         '2_56068663',
         '3_56

In [429]:
# Create a dataframe to append results to
bet_offers_df = pd.DataFrame(columns=['League', 'Game', 'StartDate', 'StartTime', 'BetLabel', 'Outcome1_Label', 
                                      'Outcome1_Line', 'Outcome1_Odds', 'Outcome2_Label', 'Outcome2_Line', 'Outcome2_Odds'])

# Find list of games to loop over to pull
games = nfl_scrape['eventGroups']['88670561']['events'].keys()

# Loop over games
for index, game in enumerate(games):
    # Set the game JSON as variable
    game_details = nfl_scrape['eventGroups']['88670561']['events'][game]
    # Parse the scrape results
    eventId = game_details['eventId']
    eventGroup = game_details['eventGroupName']
    eventGroupId = game_details['eventGroupId']
    displayGroupId = game_details['displayGroupId']
    game = game_details['name']
    teamName1 = game_details['teamName1']
    teamName1 = game_details['teamName2']
    startDate = game_details['startDate']

    # Web scrape Draft Kings for player props
    url = f"https://sportsbook.draftkings.com/event/{eventId}"
    response = requests.get(url)
    soup = BeautifulSoup(response.text, "html.parser")
    # Clean BeautifulSoup response
    # Filter out opening and closing <script> tags
    scrape = str(list(list(list(soup.children)[2])[3])[11]).replace("<script>","").replace("</script>", "")
    # Remove leading and trailing whitespace
    scrape = scrape.strip()
    # Split sections
    scrape = scrape.split(";\n")
    # Isolate to json of interest
    scrape = scrape[6].strip()
    # Format as json dictionary
    scrape = scrape.replace("window.__INITIAL_STATE__ = ","")
    scrape = json.loads(scrape)
    # Parse the scrape results
    eventGroupId = list(scrape['eventGroups'].keys())[0]
    providerEventId = list(scrape['eventGroups'][eventGroupId]['events'].keys())[0]
    providerOfferId = list(scrape['offers'][eventGroupId].keys())[0]
    eventId = scrape['eventGroups'][eventGroupId]['events'][providerEventId]['eventId']
    game_details = scrape['eventGroups'][eventGroupId]['events'][providerEventId]
    game = game_details['name']
    eventGroup = game_details['eventGroupName']
    teamName1 = game_details['teamName1']
    teamName1 = game_details['teamName2']
    startDate = game_details['startDate']
    date, time = startDate.split('T')
    dt = date + ' ' + time[:8]
    dt = datetime.strptime(dt, '%Y-%m-%d %H:%M:%S')
    # Format as right timezone (-5 hours)
    dt = dt - timedelta(hours=5)
    date = dt.strftime('%a, %b %d')
    time = dt.strftime('%I:%M %p')

    # Isolate the bet offers from the beautiful soup scrape
    offers = scrape['offers'][eventGroupId]

    # Loop over offers and add to dataframe
    for index, offer in enumerate(offers):

        # Create a list for parsing the offers 
        offers_parsed = [eventGroup, game, date, time, '', '', '', '', '', '', '']

        # Parse the betting offer
        offer_dict = scrape['offers'][eventGroupId][offer]
        try:
            providerOfferId = offer_dict['providerOfferId']
            providerId = offer_dict['providerId']
            providerEventId = offer_dict['providerEventId']
            bet_label = offer_dict['label']
            isOpen = offer_dict['isOpen']
            outcomes = offer_dict['outcomes']
        except:
            continue

        # Assign to list
        offers_parsed[4] = bet_label    

        # Extract outcomes
        if len(outcomes) == 1:

            # Parse the outcome
            outcome_label = outcomes[0]['label']
            outcome_odds = outcomes[0]['oddsAmerican']
            offers_parsed[5] = outcome_label
            offers_parsed[7] = outcome_odds

            # Append the list to the dataframe 
            bet_offers_df.loc[len(bet_offers_df)] = offers_parsed

        elif len(outcomes) == 2:

            # Parse the outcomes
            for i, x in enumerate(outcomes):
                if i == 0:
                    outcome_label = outcomes[i]['label']
                    try:
                        outcome_line = outcomes[i]['line']
                    except:
                        outcome_line = ''
                    outcome_odds = outcomes[i]['oddsAmerican']
                    offers_parsed[5] = outcome_label
                    offers_parsed[6] = outcome_line
                    offers_parsed[7] = outcome_odds
                else:
                    outcome_label = outcomes[i]['label']
                    try:
                        outcome_line = outcomes[i]['line']
                    except:
                        continue
                    outcome_odds = outcomes[i]['oddsAmerican']
                    offers_parsed[8] = outcome_label
                    offers_parsed[9] = outcome_line
                    offers_parsed[10] = outcome_odds

            # Append the list to the dataframe 
            bet_offers_df.loc[len(bet_offers_df)] = offers_parsed

        else:

            continue

bet_offers_df

League                          Game    StartDate StartTime  \
0      NFL      DAL Cowboys @ PHI Eagles  Sat, Jan 08  08:15 PM   
1      NFL      DAL Cowboys @ PHI Eagles  Sat, Jan 08  08:15 PM   
2      NFL      DAL Cowboys @ PHI Eagles  Sat, Jan 08  08:15 PM   
3      NFL      DAL Cowboys @ PHI Eagles  Sat, Jan 08  08:15 PM   
4      NFL      DAL Cowboys @ PHI Eagles  Sat, Jan 08  08:15 PM   
..     ...                           ...          ...       ...   
696    NFL  SEA Seahawks @ ARI Cardinals  Sun, Jan 09  04:25 PM   
697    NFL  SEA Seahawks @ ARI Cardinals  Sun, Jan 09  04:25 PM   
698    NFL  SEA Seahawks @ ARI Cardinals  Sun, Jan 09  04:25 PM   
699    NFL  SEA Seahawks @ ARI Cardinals  Sun, Jan 09  04:25 PM   
700    NFL  SEA Seahawks @ ARI Cardinals  Sun, Jan 09  04:25 PM   

                           BetLabel Outcome1_Label Outcome1_Line  \
0             Total Points Odd/Even            Odd                 
1                          Overtime            Yes                 
2    Both Teams to Score 10+ Points            Yes                 
3    Both Teams to Score 15+ Points            Yes                 
4    Both Teams to Score 20+ Points            Yes                 
..                              ...            ...           ...   
696     Last to Score - 1st Quarter   SEA Seahawks                 
697             1st Touchdown Yards           Over          10.5   
698                 1st Score Yards           Over          21.5   
699        Largest Lead of the Game           Over          14.5   
700      Total 3rd Down Conversions           Over          10.5   

    Outcome1_Odds Outcome2_Label Outcome2_Line Outcome2_Odds  
0            -120                                             
1           +1200                                             
2            -500                                             
3            -125                                             
4            +190                                             
..            ...            ...           ...           ...  
696          +135                                             
697          -110          Under          10.5          -115  
698          -115          Under          21.5          -110  
699          -115          Under          14.5          -115  
700          -170          Under          10.5          +100  

[701 rows x 11 columns]

In [433]:
# Save the odds file as a csv for analysis
bet_offers_df.to_csv('Data/NFLBetOdds.csv', index=False)

## NBA

In [437]:
# Web scrape Draft Kings NFL page forthe games available
url = "https://sportsbook.draftkings.com/leagues/basketball/88670846"
response = requests.get(url)
soup = BeautifulSoup(response.text, "html.parser")

In [438]:
# Narrow the Beautiful Soup extract to just the field of interest "window.__INITIAL_STATE__"

# Filter out opening and closing <script> tags
nba_scrape = str(list(list(list(soup.children)[2])[3])[11]).replace("<script>","").replace("</script>", "")
# Remove leading and trailing whitespace
nba_scrape = nba_scrape.strip()
# Split sections
nba_scrape = nba_scrape.split(";\n")
# Isolate to json of interest
nba_scrape = nba_scrape[6].strip()
# Format as json dictionary
nba_scrape = nba_scrape.replace("window.__INITIAL_STATE__ = ","")
nba_scrape = json.loads(nba_scrape)
nba_scrape

{'eventGroups': {'88670846': {'eventGroupId': 88670846,
   'providerEventGroupId': '42648',
   'providerId': 2,
   'displayGroupId': 5319,
   'name': 'NBA',
   'offerCategories': [{'name': 'Game Lines',
     'offerSubcategoryDescriptors': [{'name': 'Game',
       'offerSubcategory': {'name': 'Game',
        'subcategoryId': 4511,
        'componentId': 210,
        'betTypeIds': [1, 6, 2],
        'offerSortOrder': ['2_62534291',
         '3_62534291',
         '1_62534291',
         '2_62534263',
         '3_62534263',
         '1_62534263',
         '2_62511505',
         '3_62511505',
         '1_62511505',
         '2_62511517',
         '3_62511517',
         '1_62511517',
         '2_62511548',
         '3_62511548',
         '1_62511548']},
       'subcategoryId': 4511},
      {'name': 'Alternate Spread', 'subcategoryId': 4606},
      {'name': 'Alternate Total', 'subcategoryId': 4608},
      {'name': 'Spread/Total', 'subcategoryId': 10005},
      {'name': 'Moneyline / Total', 's

In [439]:
# Create a dataframe to append results to
bet_offers_df = pd.DataFrame(columns=['League', 'Game', 'StartDate', 'StartTime', 'BetLabel', 'Outcome1_Label', 
                                      'Outcome1_Line', 'Outcome1_Odds', 'Outcome2_Label', 'Outcome2_Line', 'Outcome2_Odds'])

# Find list of games to loop over to pull
games = nba_scrape['eventGroups']['88670846']['events'].keys()

# Loop over games
for index, game in enumerate(games):
    # Set the game JSON as variable
    game_details = nba_scrape['eventGroups']['88670846']['events'][game]
    # Parse the scrape results
    eventId = game_details['eventId']
    eventGroup = game_details['eventGroupName']
    eventGroupId = game_details['eventGroupId']
    displayGroupId = game_details['displayGroupId']
    game = game_details['name']
    teamName1 = game_details['teamName1']
    teamName1 = game_details['teamName2']
    startDate = game_details['startDate']

    # Web scrape Draft Kings for player props
    url = f"https://sportsbook.draftkings.com/event/{eventId}"
    response = requests.get(url)
    soup = BeautifulSoup(response.text, "html.parser")
    # Clean BeautifulSoup response
    # Filter out opening and closing <script> tags
    scrape = str(list(list(list(soup.children)[2])[3])[11]).replace("<script>","").replace("</script>", "")
    # Remove leading and trailing whitespace
    scrape = scrape.strip()
    # Split sections
    scrape = scrape.split(";\n")
    # Isolate to json of interest
    scrape = scrape[6].strip()
    # Format as json dictionary
    scrape = scrape.replace("window.__INITIAL_STATE__ = ","")
    scrape = json.loads(scrape)
    # Parse the scrape results
    eventGroupId = list(scrape['eventGroups'].keys())[0]
    providerEventId = list(scrape['eventGroups'][eventGroupId]['events'].keys())[0]
    providerOfferId = list(scrape['offers'][eventGroupId].keys())[0]
    eventId = scrape['eventGroups'][eventGroupId]['events'][providerEventId]['eventId']
    game_details = scrape['eventGroups'][eventGroupId]['events'][providerEventId]
    game = game_details['name']
    eventGroup = game_details['eventGroupName']
    teamName1 = game_details['teamName1']
    teamName1 = game_details['teamName2']
    startDate = game_details['startDate']
    date, time = startDate.split('T')
    dt = date + ' ' + time[:8]
    dt = datetime.strptime(dt, '%Y-%m-%d %H:%M:%S')
    # Format as right timezone (-5 hours)
    dt = dt - timedelta(hours=5)
    date = dt.strftime('%a, %b %d')
    time = dt.strftime('%I:%M %p')

    # Isolate the bet offers from the beautiful soup scrape
    offers = scrape['offers'][eventGroupId]

    # Loop over offers and add to dataframe
    for index, offer in enumerate(offers):

        # Create a list for parsing the offers 
        offers_parsed = [eventGroup, game, date, time, '', '', '', '', '', '', '']

        # Parse the betting offer
        offer_dict = scrape['offers'][eventGroupId][offer]
        try:
            providerOfferId = offer_dict['providerOfferId']
            providerId = offer_dict['providerId']
            providerEventId = offer_dict['providerEventId']
            bet_label = offer_dict['label']
            isOpen = offer_dict['isOpen']
            outcomes = offer_dict['outcomes']
        except:
            continue

        # Assign to list
        offers_parsed[4] = bet_label    

        # Extract outcomes
        if len(outcomes) == 1:

            # Parse the outcome
            outcome_label = outcomes[0]['label']
            outcome_odds = outcomes[0]['oddsAmerican']
            offers_parsed[5] = outcome_label
            offers_parsed[7] = outcome_odds

            # Append the list to the dataframe 
            bet_offers_df.loc[len(bet_offers_df)] = offers_parsed

        elif len(outcomes) == 2:

            # Parse the outcomes
            for i, x in enumerate(outcomes):
                if i == 0:
                    outcome_label = outcomes[i]['label']
                    try:
                        outcome_line = outcomes[i]['line']
                    except:
                        outcome_line = ''
                    outcome_odds = outcomes[i]['oddsAmerican']
                    offers_parsed[5] = outcome_label
                    offers_parsed[6] = outcome_line
                    offers_parsed[7] = outcome_odds
                else:
                    outcome_label = outcomes[i]['label']
                    try:
                        outcome_line = outcomes[i]['line']
                    except:
                        continue
                    outcome_odds = outcomes[i]['oddsAmerican']
                    offers_parsed[8] = outcome_label
                    offers_parsed[9] = outcome_line
                    offers_parsed[10] = outcome_odds

            # Append the list to the dataframe 
            bet_offers_df.loc[len(bet_offers_df)] = offers_parsed

        else:

            continue

bet_offers_df

League                           Game    StartDate StartTime  \
0      NBA  MEM Grizzlies @ CLE Cavaliers  Tue, Jan 04  07:11 PM   
1      NBA  MEM Grizzlies @ CLE Cavaliers  Tue, Jan 04  07:11 PM   
2      NBA  MEM Grizzlies @ CLE Cavaliers  Tue, Jan 04  07:11 PM   
3      NBA  MEM Grizzlies @ CLE Cavaliers  Tue, Jan 04  07:11 PM   
4      NBA  MEM Grizzlies @ CLE Cavaliers  Tue, Jan 04  07:11 PM   
..     ...                            ...          ...       ...   
488    NBA          SAC Kings @ LA Lakers  Tue, Jan 04  10:40 PM   
489    NBA          SAC Kings @ LA Lakers  Tue, Jan 04  10:40 PM   
490    NBA          SAC Kings @ LA Lakers  Tue, Jan 04  10:40 PM   
491    NBA          SAC Kings @ LA Lakers  Tue, Jan 04  10:40 PM   
492    NBA          SAC Kings @ LA Lakers  Tue, Jan 04  10:40 PM   

                                       BetLabel Outcome1_Label Outcome1_Line  \
0              Total Points Odd/Even - 1st Half            Odd                 
1           Total Points Odd/Even - 1st Quarter            Odd                 
2                         Total Points Odd/Even            Odd                 
3               Desmond Bane Assists + Rebounds           Over           6.5   
4                          Desmond Bane Assists           Over           2.5   
..                                          ...            ...           ...   
488                    Davion Mitchell\t Blocks           Over           0.5   
489  SAC Kings: Team Total Points - 1st Quarter           Over          28.5   
490  LA Lakers: Team Total Points - 1st Quarter           Over          30.5   
491     SAC Kings: Team Total Points - 1st Half           Over          57.5   
492     LA Lakers: Team Total Points - 1st Half           Over          61.5   

    Outcome1_Odds Outcome2_Label Outcome2_Line Outcome2_Odds  
0            -110                                             
1            -115                                             
2            -115                                             
3            -130          Under           6.5          +100  
4            -110          Under           2.5          -125  
..            ...            ...           ...           ...  
488          +380          Under           0.5          -650  
489          -115          Under          28.5          -115  
490          -120          Under          30.5          -110  
491          -105          Under          57.5          -125  
492          -105          Under          61.5          -125  

[493 rows x 11 columns]

In [440]:
# Save the odds file as a csv for analysis
bet_offers_df.to_csv('Data/NBABetOdds.csv', index=False)

## NBA and NFL 

In [484]:
# Create a dataframe to append results to
bet_offers_df = pd.DataFrame(columns=['League', 'Game', 'StartDate', 'StartTime', 'BetLabel', 'Outcome1_Label', 
                                      'Outcome1_Line', 'Outcome1_Odds', 'Outcome2_Label', 'Outcome2_Line', 'Outcome2_Odds'])

# Create a list of the DraftKings URLs to parse
urls = ["https://sportsbook.draftkings.com/leagues/basketball/88670846", 
        "https://sportsbook.draftkings.com/leagues/football/88670561"]

# Loop over the URLs and parse results
for url in urls:
    print(url)
    # Get the BeautifulSoup data from the DraftKings website
    dk_response = requests.get(url)
    dk_soup = BeautifulSoup(dk_response.text, "html.parser")

    # Narrow the Beautiful Soup extract to just the field of interest "window.__INITIAL_STATE__"

    # Filter out opening and closing <script> tags
    dk_scrape = str(list(list(list(dk_soup.children)[2])[3])[11]).replace("<script>","").replace("</script>", "")
    # Remove leading and trailing whitespace
    dk_scrape = dk_scrape.strip()
    # Split sections
    dk_scrape = dk_scrape.split(";\n")
    # Isolate to json of interest
    dk_scrape = dk_scrape[6].strip()
    # Format as json dictionary
    dk_scrape = dk_scrape.replace("window.__INITIAL_STATE__ = ","")
    dk_scrape = json.loads(dk_scrape)
    
    # Grab the sport ID from the scrape
    sportId = list(dk_scrape['eventGroups'].keys())[0]
    
    # From the full scrape of the page, pull a list of the games to loop over and extract data from
    games = dk_scrape['eventGroups'][sportId]['events'].keys()
    print("Games: ", games)
    
    # Loop over games
    for index, game in enumerate(games):
        print(game)
        # Set the game JSON as variable
        game_details = dk_scrape['eventGroups'][sportId]['events'][game]
        # Get the eventId so I can scrape the actual props
        eventId = game_details['eventId']

        # Web scrape Draft Kings for player props
        props_url = f"https://sportsbook.draftkings.com/event/{eventId}"
        response = requests.get(props_url)
        soup = BeautifulSoup(response.text, "html.parser")
        
        # Clean BeautifulSoup response
        # Filter out opening and closing <script> tags
        scrape = str(list(list(list(soup.children)[2])[3])[11]).replace("<script>","").replace("</script>", "")
        # Remove leading and trailing whitespace
        scrape = scrape.strip()
        # Split sections
        scrape = scrape.split(";\n")
        # Isolate to json of interest
        scrape = scrape[6].strip()
        # Format as json dictionary
        scrape = scrape.replace("window.__INITIAL_STATE__ = ","")
        scrape = json.loads(scrape)
        
        # Parse the scrape results
        eventGroupId = list(scrape['eventGroups'].keys())[0]
        providerEventId = list(scrape['eventGroups'][eventGroupId]['events'].keys())[0]
        providerOfferId = list(scrape['offers'][eventGroupId].keys())[0]
        eventId = scrape['eventGroups'][eventGroupId]['events'][providerEventId]['eventId']
        game_details = scrape['eventGroups'][eventGroupId]['events'][providerEventId]
        game = game_details['name']
        eventGroup = game_details['eventGroupName']
        teamName1 = game_details['teamName1']
        teamName1 = game_details['teamName2']
        startDate = game_details['startDate']
        date, time = startDate.split('T')
        dt = date + ' ' + time[:8]
        dt = datetime.strptime(dt, '%Y-%m-%d %H:%M:%S')
        # Format as right timezone (-5 hours)
        dt = dt - timedelta(hours=5)
        date = dt.strftime('%a, %b %d')
        time = dt.strftime('%I:%M %p')

        # Isolate the bet offers from the beautiful soup scrape
        offers = scrape['offers'][eventGroupId]

        # Loop over offers and add to dataframe
        for index, offer in enumerate(offers):

            # Create a list for parsing the offers 
            offers_parsed = [eventGroup, game, date, time, '', '', '', '', '', '', '']

            # Parse the betting offer
            offer_dict = scrape['offers'][eventGroupId][offer]
            try:
                providerOfferId = offer_dict['providerOfferId']
                providerId = offer_dict['providerId']
                providerEventId = offer_dict['providerEventId']
                bet_label = offer_dict['label']
                isOpen = offer_dict['isOpen']
                outcomes = offer_dict['outcomes']
            except:
                continue

            # Assign to list
            offers_parsed[4] = bet_label    

            # Extract outcomes
            if len(outcomes) == 1:

                # Parse the outcome
                outcome_label = outcomes[0]['label']
                outcome_odds = outcomes[0]['oddsAmerican']
                offers_parsed[5] = outcome_label
                offers_parsed[7] = outcome_odds

                # Append the list to the dataframe 
                bet_offers_df.loc[len(bet_offers_df)] = offers_parsed

            elif len(outcomes) == 2:

                # Parse the outcomes
                for i, x in enumerate(outcomes):
                    if i == 0:
                        outcome_label = outcomes[i]['label']
                        try:
                            outcome_line = outcomes[i]['line']
                        except:
                            outcome_line = ''
                        outcome_odds = outcomes[i]['oddsAmerican']
                        offers_parsed[5] = outcome_label
                        offers_parsed[6] = outcome_line
                        offers_parsed[7] = outcome_odds
                    else:
                        outcome_label = outcomes[i]['label']
                        try:
                            outcome_line = outcomes[i]['line']
                        except:
                            continue
                        outcome_odds = outcomes[i]['oddsAmerican']
                        offers_parsed[8] = outcome_label
                        offers_parsed[9] = outcome_line
                        offers_parsed[10] = outcome_odds

                # Append the list to the dataframe 
                bet_offers_df.loc[len(bet_offers_df)] = offers_parsed

            else:

                continue

bet_offers_df

https://sportsbook.draftkings.com/leagues/basketball/88670846
Games:  dict_keys(['25913984', '25913985', '25913987', '25913998', '25914010'])
25913984
25913985
25913987
25913998
25914010
https://sportsbook.draftkings.com/leagues/football/88670561
Games:  dict_keys(['22932871', '22932873', '22932877', '22932886', '22932889', '22932890', '22932891', '22932894', '22932895', '22932896', '22932897', '22932898', '22932907', '22932908', '22932909', '22932910'])
22932871
22932873
22932877
22932886
22932889
22932890
22932891
22932894
22932895
22932896
22932897
22932898
22932907
22932908
22932909
22932910


League                           Game    StartDate StartTime  \
0       NBA  MEM Grizzlies @ CLE Cavaliers  Tue, Jan 04  07:11 PM   
1       NBA  MEM Grizzlies @ CLE Cavaliers  Tue, Jan 04  07:11 PM   
2       NBA  MEM Grizzlies @ CLE Cavaliers  Tue, Jan 04  07:11 PM   
3       NBA  MEM Grizzlies @ CLE Cavaliers  Tue, Jan 04  07:11 PM   
4       NBA  MEM Grizzlies @ CLE Cavaliers  Tue, Jan 04  07:11 PM   
...     ...                            ...          ...       ...   
1188    NFL   SEA Seahawks @ ARI Cardinals  Sun, Jan 09  04:25 PM   
1189    NFL   SEA Seahawks @ ARI Cardinals  Sun, Jan 09  04:25 PM   
1190    NFL   SEA Seahawks @ ARI Cardinals  Sun, Jan 09  04:25 PM   
1191    NFL   SEA Seahawks @ ARI Cardinals  Sun, Jan 09  04:25 PM   
1192    NFL   SEA Seahawks @ ARI Cardinals  Sun, Jan 09  04:25 PM   

                                 BetLabel Outcome1_Label Outcome1_Line  \
0        Total Points Odd/Even - 1st Half            Odd                 
1     Total Points Odd/Even - 2nd Quarter            Odd                 
2                   Total Points Odd/Even            Odd                 
3         Desmond Bane Assists + Rebounds           Over           7.5   
4                    Desmond Bane Assists           Over           1.5   
...                                   ...            ...           ...   
1188          Last to Score - 1st Quarter   SEA Seahawks                 
1189                  1st Touchdown Yards           Over          10.5   
1190                      1st Score Yards           Over          21.5   
1191             Largest Lead of the Game           Over          14.5   
1192           Total 3rd Down Conversions           Over          10.5   

     Outcome1_Odds Outcome2_Label Outcome2_Line Outcome2_Odds  
0             -115                                             
1             -105                                             
2             -120                                             
3             +105          Under           7.5          -140  
4             -185          Under           1.5          +140  
...            ...            ...           ...           ...  
1188          +135                                             
1189          -110          Under          10.5          -115  
1190          -115          Under          21.5          -110  
1191          -115          Under          14.5          -115  
1192          -170          Under          10.5          +100  

[1193 rows x 11 columns]

In [485]:
# Save the odds file as a csv for analysis
bet_offers_df.to_csv('Data/BetOdds.csv', index=False)